In [13]:
import pandas as pd
import requests as req
from bs4 import BeautifulSoup as bs
import re
import json
import numpy as np
import warnings
warnings.filterwarnings('ignore')
import csv
pd.set_option('display.max_rows', None) 
pd.set_option('display.max_columns', None) 
from selenium import webdriver
import time
%pip install webdriver-manager
from selenium import webdriver
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager

Note: you may need to restart the kernel to use updated packages.


In [14]:
from selenium.webdriver.chrome.options import Options
opciones=Options()
# quita la bandera de ser robot
opciones.add_experimental_option('excludeSwitches', ['enable-automation'])
opciones.add_experimental_option('useAutomationExtension', False)
opciones.headless=False   # si True, no aparece la ventana (headless=no visible)
opciones.add_argument('--start-maximized')         # comienza maximizado
#opciones.add_extension('driver/adblock.crx')       # adblocker
#opciones.add_argument('user-data-dir=selenium')    # mantiene las coockies
opciones.add_argument('--incognito')              # incognito


In [15]:
def tirania(url):
    
    PATH=ChromeDriverManager().install()
    driver=webdriver.Chrome(PATH) 
    driver.get(url)
    time.sleep(8)
    
    
    df=pd.DataFrame(columns=['Beach','Date','Hour','Wind_speed','Gust','Wave','Period','Temperature','Wind_direction','Wave_direction'])
    
    
    date=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_dates"]').text.split()

    lst=[]
    for e in range(0,len(date)+3,3):
        var=''.join(date[e-2]).replace('.','')
        lst.append(var)

    lst.pop(0)  

    for e in range(len(lst)):
        df['Date']=lst

    time.sleep(6)

    hour=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_dates"]').text.split()
    lst2=[]
    for e in range(0,len(date)+3,3):
        var=''.join(date[e-1:e])
        lst2.append(var)
    lst2.pop(0)    
    for e in range(len(lst2)):
        df['Hour']=lst2

    time.sleep(5)

    playa=driver.find_element(By.XPATH, '//*[@id="forecasts-page-content"]/div[2]/div[1]/a[1]/div').text

    for e in range(len(df.Hour)):
        df['Beach']=playa

    time.sleep(4)

    
    velocidad=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_WINDSPD"]').text.split()

    for e in range(len(velocidad)):
        df['Wind_speed']=velocidad

    rafagas=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_GUST"]').text.split()

    for e in range(len(rafagas)):
        df['Gust']=rafagas
    
    ola=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_HTSGW"]').text.split()
    
    
    for e in range(len(ola)):
        if ola=='':
    
            df['Wave']=''
        else:
            df['Wave']=ola

    
    periodo=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_PERPW"]').text

    if len(periodo)>0:
        periodo=periodo.split()[0]
        df['Period']=periodo

    elif len(periodo)<=0:
        df['Period']=periodo


    
    temp=driver.find_element(By.XPATH, '//*[@id="tabid_0_0_TMP"]').text.split()

    for e in range(len(temp)):
        df['Temperature']=temp

    direc_viento=driver.find_elements(By.XPATH, '//*[@id="tabid_0_0_SMER"]')

    for f in direc_viento:
        elementos=f.find_elements(By.TAG_NAME, 'span')
        tmp=[]

        for e in elementos:
            tmp.append(e.get_attribute('title'))
        tmp.append(url.split('/')[-1])
    

    tmp.pop()
    df['Wind_direction']=tmp

    direc_ola=driver.find_elements(By.XPATH, '//*[@id="tabid_0_0_DIRPW"]')
    

    for f in direc_ola:

        elementos=f.find_elements(By.TAG_NAME, 'span')

        tmp2=[]
        for e in elementos:

            #tmp2.append(e.get_attribute('title'))

            mequetrefe=e.get_attribute('title')

            tmp2.append(mequetrefe)


        if len(mequetrefe)>0:   
            tmp2.append(url.split('/')[-1])

        else:
            mequetrefe=''

    if len(tmp2)>1:
        tmp2.pop()    
        df['Wave_direction']=tmp2
    else:
        df['Wave_direction']=mequetrefe
    

    
        
        
        
        

    
    #time.sleep(8)
    
    #loca=driver.find_element(By.XPATH, '//*[@id="forecasts-page-content"]/div[2]/div[1]/div[2]/ul/li[4]/a').text[:-8]
    
    #for e in range(len(loca)):
        #df['Location']=loca
    
    
  
        
    
  


    return df


In [6]:
    tirania('https://www.windguru.cz/48686')

Beach Date Hour Wind_speed Gust Wave Period Temperature  \
0   Spain - Hondarribia   13  07h          7   12  2.2      9          13   
1   Spain - Hondarribia   13  09h          4    6  2.1      9          13   
2   Spain - Hondarribia   13  11h          4    6  1.8      9          14   
3   Spain - Hondarribia   13  13h          3    7  1.5      9          16   
4   Spain - Hondarribia   13  15h          4    7  1.3      9          17   
5   Spain - Hondarribia   13  17h          7   11  1.1      9          17   
6   Spain - Hondarribia   13  19h          8   15    1      9          16   
7   Spain - Hondarribia   13  21h          6   12  0.9      9          16   
8   Spain - Hondarribia   14  03h          6   13  0.8      9          16   
9   Spain - Hondarribia   14  05h          4   10  0.8      9          15   
10  Spain - Hondarribia   14  07h          4    7  0.8      9          13   
11  Spain - Hondarribia   14  09h          5    7  0.8      9          14   
12  Spain - Hondarribia   14  11h          6   11  0.8      9          15   
13  Spain - Hondarribia   14  13h          4    9  0.8      9          17   
14  Spain - Hondarribia   14  15h          3    8  0.9      9          17   
15  Spain - Hondarribia   14  17h          6    9  1.1      9          16   
16  Spain - Hondarribia   14  19h          7   13  1.1      9          16   
17  Spain - Hondarribia   14  21h          6   11  1.1      9          14   
18  Spain - Hondarribia   15  03h          7   13  1.1      9          14   
19  Spain - Hondarribia   15  05h          7   13  1.2      9          13   
20  Spain - Hondarribia   15  07h          7   12  1.2      9          12   
21  Spain - Hondarribia   15  09h          8   14  1.2      9          12   
22  Spain - Hondarribia   15  11h          9   16  1.1      9          14   
23  Spain - Hondarribia   15  13h          8   14  1.1      9          15   
24  Spain - Hondarribia   15  15h          8   13  1.1      9          14   
25  Spain - Hondarribia   15  17h          8   14  1.4      9          13   
26  Spain - Hondarribia   15  19h          6   12  1.5      9          13   
27  Spain - Hondarribia   15  21h          6   10  1.5      9          12   
28  Spain - Hondarribia   16  03h          6   12  1.4      9          12   
29  Spain - Hondarribia   16  05h          5   12  1.5      9          12   
30  Spain - Hondarribia   16  07h          7   11  1.6      9          11   
31  Spain - Hondarribia   16  09h          8   13  1.7      9          11   
32  Spain - Hondarribia   16  11h          8   11  1.5      9          10   
33  Spain - Hondarribia   16  13h          9   13  1.4      9          10   
34  Spain - Hondarribia   16  15h          9   14  1.3      9          10   
35  Spain - Hondarribia   16  17h         10   13  1.2      9           9   
36  Spain - Hondarribia   16  19h          9   11  1.2      9           9   
37  Spain - Hondarribia   16  22h          4    6    1      9          10   
38  Spain - Hondarribia   17  04h          3    4  0.8      9           9   
39  Spain - Hondarribia   17  06h          3    5  0.7      9           9   
40  Spain - Hondarribia   17  08h          3    5  0.7      9           8   
41  Spain - Hondarribia   17  10h          3    5  0.6      9           9   
42  Spain - Hondarribia   17  12h          2    5  0.5      9          10   
43  Spain - Hondarribia   17  14h          2    5  0.5      9          11   
44  Spain - Hondarribia   17  16h          3    5  0.4      9          12   
45  Spain - Hondarribia   17  18h          4    5  0.4      9          11   
46  Spain - Hondarribia   17  20h          5    6  0.3      9          10   
47  Spain - Hondarribia   17  22h          5    6  0.3      9           9   
48  Spain - Hondarribia   18  04h          8   10  0.4      9          11   
49  Spain - Hondarribia   18  06h          8    8  0.4      9          10   
50  Spain - Hondarribia   18  08h          8   16  0.4      9          10   
51  Spain - Ho

In [16]:
%pip install joblib

Note: you may need to restart the kernel to use updated packages.


In [17]:
from joblib import Parallel, delayed

In [9]:

links=['https://www.windguru.cz/48686',
'https://www.windguru.cz/501079',
'https://www.windguru.cz/501080',
'https://www.windguru.cz/696275',
'https://www.windguru.cz/48688',
'https://www.windguru.cz/4903',
'https://www.windguru.cz/48690',
'https://www.windguru.cz/53313']


lst_playas=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:  1.2min remaining:  3.6min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:  1.2min finished


In [10]:
playas=pd.concat(lst_playas)
playas

Beach Date Hour Wind_speed Gust  \
0                              Spain - Hondarribia   13  07h          7   12   
1                              Spain - Hondarribia   13  09h          4    6   
2                              Spain - Hondarribia   13  11h          4    6   
3                              Spain - Hondarribia   13  13h          3    7   
4                              Spain - Hondarribia   13  15h          4    7   
5                              Spain - Hondarribia   13  17h          7   11   
6                              Spain - Hondarribia   13  19h          8   15   
7                              Spain - Hondarribia   13  21h          6   12   
8                              Spain - Hondarribia   14  03h          6   13   
9                              Spain - Hondarribia   14  05h          4   10   
10                             Spain - Hondarribia   14  07h          4    7   
11                             Spain - Hondarribia   14  09h          5    7   
12                             Spain - Hondarribia   14  11h          6   11   
13                             Spain - Hondarribia   14  13h          4    9   
14                             Spain - Hondarribia   14  15h          3    8   
15                             Spain - Hondarribia   14  17h          6    9   
16                             Spain - Hondarribia   14  19h          7   13   
17                             Spain - Hondarribia   14  21h          6   11   
18                             Spain - Hondarribia   15  03h          7   13   
19                             Spain - Hondarribia   15  05h          7   13   
20                             Spain - Hondarribia   15  07h          7   12   
21                             Spain - Hondarribia   15  09h          8   14   
22                             Spain - Hondarribia   15  11h          9   16   
23                             Spain - Hondarribia   15  13h          8   14   
24                             Spain - Hondarribia   15  15h          8   13   
25                             Spain - Hondarribia   15  17h          8   14   
26                             Spain - Hondarribia   15  19h          6   12   
27                             Spain - Hondarribia   15  21h          6   10   
28                             Spain - Hondarribia   16  03h          6   12   
29                             Spain - Hondarribia   16  05h          5   12   
30                             Spain - Hondarribia   16  07h          7   11   
31                             Spain - Hondarribia   16  09h          8   13   
32                             Spain - Hondarribia   16  11h          8   11   
33                             Spain - Hondarribia   16  13h          9   13   
34                             Spain - Hondarribia   16  15h          9   14   
35                             Spain - Hondarribia   16  17h         10   13   
36                             Spain - Hondarribia   16  19h          9   11   
37                             Spain - Hondarribia   16  22h          4    6   
38                             Spain - Hondarribia   17  04h          3    4   
39                             Spain - Hondarribia   17  06h          3    5   
40                             Spain - Hondarribia   17  08h          3    5   
41                             Spain - Hondarribia   17  10h          3    5   
42                             Spain - Hondarribia   17  12h          2    5   
43                             Spain - Hondarribia   17  14h          2    5   
44                             Spain - Hondarribia   17  16h          3    5   
45                             Spain - Hondarribia   17  18h          4    5   
46                             Spain - Hondarribia   17  20h          5    6   
47                             Spain - Hondarribia   17  22h          5    6   
48                             Spain - Hondarribia   18  04h          8   10   
49                             Spain - Hondar

In [49]:
links2=['https://www.windguru.cz/48687',
'https://www.windguru.cz/48689',
'https://www.windguru.cz/48692',
'https://www.windguru.cz/48691',
'https://www.windguru.cz/501076',
'https://www.windguru.cz/47715',
'https://www.windguru.cz/11040',
'https://www.windguru.cz/501082']

links3=['https://www.windguru.cz/48694',
'https://www.windguru.cz/48695',
'https://www.windguru.cz/48696',
'https://www.windguru.cz/48698',
'https://www.windguru.cz/48702',
'https://www.windguru.cz/207059',
'https://www.windguru.cz/48701',
'https://www.windguru.cz/48699']

links4=['https://www.windguru.cz/332103',
'https://www.windguru.cz/48704',
'https://www.windguru.cz/48705',
'https://www.windguru.cz/48706',
'https://www.windguru.cz/48707',
'https://www.windguru.cz/48708',
'https://www.windguru.cz/356406',
'https://www.windguru.cz/501095']

links5=['https://www.windguru.cz/48710',
'https://www.windguru.cz/48711',
'https://www.windguru.cz/501091',
'https://www.windguru.cz/222022',
'https://www.windguru.cz/48713',
'https://www.windguru.cz/501093',
'https://www.windguru.cz/329634']

links6=['https://www.windguru.cz/501096',
'https://www.windguru.cz/501103',
'https://www.windguru.cz/501104',
'https://www.windguru.cz/501105',
'https://www.windguru.cz/501106',
'https://www.windguru.cz/501107',
'https://www.windguru.cz/48716',
'https://www.windguru.cz/356413',
'https://www.windguru.cz/48717',
'https://www.windguru.cz/48718']

links7=['https://www.windguru.cz/48719',
        'https://www.windguru.cz/48720',
        'https://www.windguru.cz/48721',
        'https://www.windguru.cz/212',
        'https://www.windguru.cz/48723',
        'https://www.windguru.cz/48725',
        'https://www.windguru.cz/48726',
        'https://www.windguru.cz/48727',
        'https://www.windguru.cz/48728',
        'https://www.windguru.cz/501108']



linksCN=['https://www.windguru.cz/103501',
         'https://www.windguru.cz/73233',
'https://www.windguru.cz/501283',
'https://www.windguru.cz/49328',
'https://www.windguru.cz/501286',
'https://www.windguru.cz/501281',
'https://www.windguru.cz/49337',  
'https://www.windguru.cz/49335',
'https://www.windguru.cz/49334']
        
       



In [13]:
lst_playas2=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links2)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:   55.3s remaining:  2.8min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:   57.3s finished


In [14]:
playas2=pd.concat(lst_playas2)
playas2

Beach Date Hour Wind_speed Gust Wave Period  \
0            Spain - Zurriola   13  07h          5    8    2      9   
1            Spain - Zurriola   13  09h          3    5  1.8      9   
2            Spain - Zurriola   13  11h          3    5  1.5      9   
3            Spain - Zurriola   13  13h          3    8  1.3      9   
4            Spain - Zurriola   13  15h          5    9  1.1      9   
5            Spain - Zurriola   13  17h          5   10  0.9      9   
6            Spain - Zurriola   13  19h          8   13  0.9      9   
7            Spain - Zurriola   13  21h          8   13  0.8      9   
8            Spain - Zurriola   14  03h          4    9  0.7      9   
9            Spain - Zurriola   14  05h          4    6  0.7      9   
10           Spain - Zurriola   14  07h          5    8  0.7      9   
11           Spain - Zurriola   14  09h          6   12  0.8      9   
12           Spain - Zurriola   14  11h          7   14  0.8      9   
13           Spain - Zurriola   14  13h          6   11  0.7      9   
14           Spain - Zurriola   14  15h          8   12  0.9      9   
15           Spain - Zurriola   14  17h          7   14    1      9   
16           Spain - Zurriola   14  19h          9   16    1      9   
17           Spain - Zurriola   14  21h          6   12    1      9   
18           Spain - Zurriola   15  03h          7   12    1      9   
19           Spain - Zurriola   15  05h          7   13    1      9   
20           Spain - Zurriola   15  07h          6   13  1.1      9   
21           Spain - Zurriola   15  09h          8   15    1      9   
22           Spain - Zurriola   15  11h          8   14    1      9   
23           Spain - Zurriola   15  13h          6    9    1      9   
24           Spain - Zurriola   15  15h          6   10    1      9   
25           Spain - Zurriola   15  17h          6   10  1.2      9   
26           Spain - Zurriola   15  19h          5    9  1.3      9   
27           Spain - Zurriola   15  21h          5    8  1.3      9   
28           Spain - Zurriola   16  03h          5    8  1.4      9   
29           Spain - Zurriola   16  05h          6    8  1.7      9   
30           Spain - Zurriola   16  07h          7   10  1.8      9   
31           Spain - Zurriola   16  09h          8   12  1.8      9   
32           Spain - Zurriola   16  11h          7   11  1.7      9   
33           Spain - Zurriola   16  13h          9   13  1.6      9   
34           Spain - Zurriola   16  15h          8   13  1.4      9   
35           Spain - Zurriola   16  17h          9   12  1.4      9   
36           Spain - Zurriola   16  19h          9   11  1.3      9   
37           Spain - Zurriola   16  22h          4    6  1.1      9   
38           Spain - Zurriola   17  04h          2    3  0.9      9   
39           Spain - Zurriola   17  06h          2    3  0.8      9   
40           Spain - Zurriola   17  08h          3    4  0.7      9   
41           Spain - Zurriola   17  10h          3    5  0.7      9   
42           Spain - Zurriola   17  12h          3    5  0.6      9   
43           Spain - Zurriola   17  14h          3    5  0.5      9   
44           Spain - Zurriola   17  16h          3    5  0.5      9   
45           Spain - Zurriola   17  18h          4    5  0.4      9   
46           Spain - Zurriola   17  20h          4    5  0.4      9   
47           Spain - Zurriola   17  22h          5    6  0.4      9   
48           Spain - Zurriola   18  04h          6   10  0.5      9   
49           Spain - Zurriola   18  06h          7    8  0.5      9   
50           Spain - Zurriola   18  08h          7   10  0.6      9   
51           Spain - Zurriola   18  10h         12   25  0.7      9   
52           Spain - Zurriola   18  12h         11   24  0.7      9   
53           Spain - Zurriola   18  14h         13   26  0.7      9   
54           Spain - Zurriola   18  16h         13   27  0.7      9   
55           Spain - Zurriola   18  18h         

In [15]:
lst_playas3=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links3)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:  1.0min remaining:  3.1min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:  1.1min finished


In [16]:
playas3=pd.concat(lst_playas3)
playas3

Beach Date Hour Wind_speed Gust Wave Period  \
0                         Spain - Somo   13  07h          4    4  2.1      9   
1                         Spain - Somo   13  09h          3    4  1.7      9   
2                         Spain - Somo   13  11h          2    6  1.4      9   
3                         Spain - Somo   13  13h          3    4  1.2      9   
4                         Spain - Somo   13  15h          2    4  1.1      9   
5                         Spain - Somo   13  17h          2    3    1      9   
6                         Spain - Somo   13  19h          3    4  0.9      9   
7                         Spain - Somo   13  21h          3    6  0.8      9   
8                         Spain - Somo   14  03h          7    9  0.8      9   
9                         Spain - Somo   14  05h          4    6  0.8      9   
10                        Spain - Somo   14  07h          3    6  0.7      9   
11                        Spain - Somo   14  09h          5    8  0.9      9   
12                        Spain - Somo   14  11h          4    8  1.1      9   
13                        Spain - Somo   14  13h          9   14  1.2      9   
14                        Spain - Somo   14  15h          8   13  1.1      9   
15                        Spain - Somo   14  17h          8   16  1.1      9   
16                        Spain - Somo   14  19h          7   14  1.1      9   
17                        Spain - Somo   14  21h          5    9  1.1      9   
18                        Spain - Somo   15  03h          6   12  1.2      9   
19                        Spain - Somo   15  05h          5   11  1.2      9   
20                        Spain - Somo   15  07h          6    9  1.2      9   
21                        Spain - Somo   15  09h          4    6  1.1      9   
22                        Spain - Somo   15  11h          4    8    1      9   
23                        Spain - Somo   15  13h          5    9  1.2      9   
24                        Spain - Somo   15  15h          6   10  1.3      9   
25                        Spain - Somo   15  17h          5   10  1.3      9   
26                        Spain - Somo   15  19h          4    8  1.3      9   
27                        Spain - Somo   15  21h          4    8  1.4      9   
28                        Spain - Somo   16  03h          4    6  2.1      9   
29                        Spain - Somo   16  05h          5    9  2.1      9   
30                        Spain - Somo   16  07h          7   12    2      9   
31                        Spain - Somo   16  09h          9   13  1.9      9   
32                        Spain - Somo   16  11h          7   11  1.8      9   
33                        Spain - Somo   16  13h          6   10  1.7      9   
34                        Spain - Somo   16  15h          6    8  1.6      9   
35                        Spain - Somo   16  17h          7    9  1.5      9   
36                        Spain - Somo   16  19h          6    8  1.5      9   
37                        Spain - Somo   16  22h          4    7  1.3      9   
38                        Spain - Somo   17  04h          4    8    1      9   
39                        Spain - Somo   17  06h          4    8    1      9   
40                        Spain - Somo   17  08h          4    7  0.9      9   
41                        Spain - Somo   17  10h          4    5  0.8      9   
42                        Spain - Somo   17  12h          3    5  0.7      9   
43                        Spain - Somo   17  14h          3    5  0.6      9   
44                        Spain - Somo   17  16h          4    6  0.6      9   
45                        Spain - Somo   17  18h          4    6  0.5      9   
46                        Spain - Somo   17  20h          4    5  0.5      9   
47                        Spain - Somo   17  22h          4    5  0.5      9   
48                        Spain - Somo   18  04h          5    7  0.4      9   
49                        Spain -

In [17]:
lst_playas4=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links4)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   2 out of   8 | elapsed:   58.1s remaining:  2.9min
[Parallel(n_jobs=-1)]: Done   8 out of   8 | elapsed:   59.4s finished


In [18]:
playas4=pd.concat(lst_playas4)
playas4

Beach Date Hour Wind_speed Gust Wave Period  \
0            Spain - Ribadesella   13  07h          5    6  1.4     15   
1            Spain - Ribadesella   13  09h          4    7  1.2     15   
2            Spain - Ribadesella   13  11h          2    4  1.1     15   
3            Spain - Ribadesella   13  13h          2    3    1     15   
4            Spain - Ribadesella   13  15h          4    5  0.9     15   
5            Spain - Ribadesella   13  17h          3    5  0.8     15   
6            Spain - Ribadesella   13  19h          3    4  0.8     15   
7            Spain - Ribadesella   13  21h          5    7  0.7     15   
8            Spain - Ribadesella   14  03h          5    6  0.7     15   
9            Spain - Ribadesella   14  05h          4    6  0.7     15   
10           Spain - Ribadesella   14  07h          5    8  0.9     15   
11           Spain - Ribadesella   14  09h          5   10  0.9     15   
12           Spain - Ribadesella   14  11h          4    7  0.9     15   
13           Spain - Ribadesella   14  13h          6   12  0.9     15   
14           Spain - Ribadesella   14  15h          4   10  0.9     15   
15           Spain - Ribadesella   14  17h          4    9  0.9     15   
16           Spain - Ribadesella   14  19h          5    8    1     15   
17           Spain - Ribadesella   14  21h          5    9    1     15   
18           Spain - Ribadesella   15  03h          7   10    1     15   
19           Spain - Ribadesella   15  05h          6    9    1     15   
20           Spain - Ribadesella   15  07h          6    8  0.9     15   
21           Spain - Ribadesella   15  09h          6    7  0.9     15   
22           Spain - Ribadesella   15  11h          4    7  0.9     15   
23           Spain - Ribadesella   15  13h          4    8  0.9     15   
24           Spain - Ribadesella   15  15h          4    8    1     15   
25           Spain - Ribadesella   15  17h          4    8  1.1     15   
26           Spain - Ribadesella   15  19h          5    7  1.3     15   
27           Spain - Ribadesella   15  21h          5    8  1.6     15   
28           Spain - Ribadesella   16  03h          4    5  2.4     15   
29           Spain - Ribadesella   16  05h          6    7  2.4     15   
30           Spain - Ribadesella   16  07h          6    8  2.3     15   
31           Spain - Ribadesella   16  09h          9   14  2.2     15   
32           Spain - Ribadesella   16  11h          9   14  2.1     15   
33           Spain - Ribadesella   16  13h          6   10  1.9     15   
34           Spain - Ribadesella   16  15h          6    8  1.8     15   
35           Spain - Ribadesella   16  17h          6    7  1.7     15   
36           Spain - Ribadesella   16  19h          6    7  1.6     15   
37           Spain - Ribadesella   16  22h          9   12  1.5     15   
38           Spain - Ribadesella   17  04h          7    8  1.2     15   
39           Spain - Ribadesella   17  06h          5    6  1.2     15   
40           Spain - Ribadesella   17  08h          4    5  1.1     15   
41           Spain - Ribadesella   17  10h          3    4    1     15   
42           Spain - Ribadesella   17  12h          3    4  0.9     15   
43           Spain - Ribadesella   17  14h          3    4  0.8     15   
44           Spain - Ribadesella   17  16h          4    5  0.7     15   
45           Spain - Ribadesella   17  18h          4    5  0.6     15   
46           Spain - Ribadesella   17  20h          4    5  0.6     15   
47           Spain - Ribadesella   17  22h          4    5  0.6     15   
48           Spain - Ribadesella   18  04h          5    6  0.5     15   
49           Spain - Ribadesella   18  06h          7    5  0.5     15   
50           Spain - Ribadesella   18  08h          6    7  0.5     15   
51           Spain - Ribadesella   18  10h          7   21  0.4     15   
52           Spain - Ribadesella   18  12h         11   22  0.4     15   
53           Spain - Ribadesell

In [19]:
lst_playas5=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links5)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   7 out of   7 | elapsed:   50.4s finished


In [20]:
playas5=pd.concat(lst_playas5)
playas5

Beach Date Hour Wind_speed Gust Wave Period  \
0              Spain - Salinas   13  07h          3    7  1.7     14   
1              Spain - Salinas   13  09h          3    7  1.5     14   
2              Spain - Salinas   13  11h          3    6  1.4     14   
3              Spain - Salinas   13  13h          3    5  1.3     14   
4              Spain - Salinas   13  15h          3    6  1.2     14   
5              Spain - Salinas   13  17h          3    5  1.1     14   
6              Spain - Salinas   13  19h          3    6  1.1     14   
7              Spain - Salinas   13  21h          3    7  1.1     14   
8              Spain - Salinas   14  03h          4    8  1.3     14   
9              Spain - Salinas   14  05h          3    7  1.4     14   
10             Spain - Salinas   14  07h          3    7  1.3     14   
11             Spain - Salinas   14  09h          5    7  1.3     14   
12             Spain - Salinas   14  11h          5    9  1.3     14   
13             Spain - Salinas   14  13h          4    9  1.3     14   
14             Spain - Salinas   14  15h          4    9  1.3     14   
15             Spain - Salinas   14  17h          4    6  1.4     14   
16             Spain - Salinas   14  19h          4    6  1.5     14   
17             Spain - Salinas   14  21h          4    7  1.6     14   
18             Spain - Salinas   15  03h          4    7  1.5     14   
19             Spain - Salinas   15  05h          4    7  1.4     14   
20             Spain - Salinas   15  07h          3    6  1.3     14   
21             Spain - Salinas   15  09h          4    7  1.2     14   
22             Spain - Salinas   15  11h          3    7  1.3     14   
23             Spain - Salinas   15  13h          2    6  1.3     14   
24             Spain - Salinas   15  15h          3    5  1.3     14   
25             Spain - Salinas   15  17h          3    6  1.4     14   
26             Spain - Salinas   15  19h          3    4  1.7     14   
27             Spain - Salinas   15  21h          3    4  2.2     14   
28             Spain - Salinas   16  03h          6   11  2.7     14   
29             Spain - Salinas   16  05h          5   10  2.6     14   
30             Spain - Salinas   16  07h          5   10  2.5     14   
31             Spain - Salinas   16  09h          7   14  2.4     14   
32             Spain - Salinas   16  11h          8   15  2.2     14   
33             Spain - Salinas   16  13h          6   13  2.1     14   
34             Spain - Salinas   16  15h          6   11    2     14   
35             Spain - Salinas   16  17h          5    9  1.9     14   
36             Spain - Salinas   16  19h          4    7  1.8     14   
37             Spain - Salinas   16  22h          4    8  1.7     14   
38             Spain - Salinas   17  04h          3    5  1.3     14   
39             Spain - Salinas   17  06h          3    5  1.2     14   
40             Spain - Salinas   17  08h          3    5  1.1     14   
41             Spain - Salinas   17  10h          3    5    1     14   
42             Spain - Salinas   17  12h          2    4  0.9     14   
43             Spain - Salinas   17  14h          2    4  0.8     14   
44             Spain - Salinas   17  16h          2    4  0.8     14   
45             Spain - Salinas   17  18h          2    3  0.7     14   
46             Spain - Salinas   17  20h          3    4  0.7     14   
47             Spain - Salinas   17  22h          4    6  0.7     14   
48             Spain - Salinas   18  04h          4    7  0.6     14   
49             Spain - Salinas   18  06h          5    5  0.6     14   
50             Spain - Salinas   18  08h          3    5  0.6     14   
51             Spain - Salinas   18  10h          5    7  0.6     14   
52             Spain - Salinas   18  12h          6   10  0.7     14   
53             Spain - Salinas   18  14h          6   10  0.8     14   
54             Spain - Salinas   18  16h          6    7    1    

In [22]:
lst_playas6=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links6)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   6 out of  10 | elapsed:  1.0min remaining:   40.9s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:  1.5min finished


In [23]:
playas6=pd.concat(lst_playas6)
playas6

Beach Date Hour Wind_speed Gust Wave Period Temperature  \
0   Spain - Foz, La Charca   13  07h          6   15  1.5     14          15   
1   Spain - Foz, La Charca   13  09h          6   13  1.4     14          16   
2   Spain - Foz, La Charca   13  11h          8   15  1.4     14          16   
3   Spain - Foz, La Charca   13  13h          8   17  1.3     14          17   
4   Spain - Foz, La Charca   13  15h          8   17  1.2     14          18   
5   Spain - Foz, La Charca   13  17h          6    9  1.2     14          17   
6   Spain - Foz, La Charca   13  19h          7   13  1.1     14          16   
7   Spain - Foz, La Charca   13  21h          7   14  1.1     14          16   
8   Spain - Foz, La Charca   14  03h          9   21  1.2     14          15   
9   Spain - Foz, La Charca   14  05h          9   19  1.2     14          15   
10  Spain - Foz, La Charca   14  07h          9   19  1.2     14          14   
11  Spain - Foz, La Charca   14  09h         11   24  1.3     14          15   
12  Spain - Foz, La Charca   14  11h         11   24  1.3     14          15   
13  Spain - Foz, La Charca   14  13h         12   25  1.3     14          16   
14  Spain - Foz, La Charca   14  15h         11   23  1.4     14          17   
15  Spain - Foz, La Charca   14  17h          9   21  1.5     14          16   
16  Spain - Foz, La Charca   14  19h          8   19  1.6     14          15   
17  Spain - Foz, La Charca   14  21h          5   11  1.6     14          13   
18  Spain - Foz, La Charca   15  03h          4   12  1.4     14          11   
19  Spain - Foz, La Charca   15  05h          5   11  1.3     14          11   
20  Spain - Foz, La Charca   15  07h          6   12  1.3     14          11   
21  Spain - Foz, La Charca   15  09h          5   10  1.3     14          11   
22  Spain - Foz, La Charca   15  11h          4    9  1.3     14          12   
23  Spain - Foz, La Charca   15  13h          3    6  1.2     14          14   
24  Spain - Foz, La Charca   15  15h          3    6  1.3     14          14   
25  Spain - Foz, La Charca   15  17h          4    5  1.4     14          13   
26  Spain - Foz, La Charca   15  19h          3    4  1.7     14          12   
27  Spain - Foz, La Charca   15  21h          3    4  2.2     14          11   
28  Spain - Foz, La Charca   16  03h          6   10  2.6     14          10   
29  Spain - Foz, La Charca   16  05h          9   13  2.6     14          10   
30  Spain - Foz, La Charca   16  07h         14   20  2.6     14          11   
31  Spain - Foz, La Charca   16  09h         14   22  2.5     14          11   
32  Spain - Foz, La Charca   16  11h         13   19  2.4     14          11   
33  Spain - Foz, La Charca   16  13h         13   18  2.3     14          11   
34  Spain - Foz, La Charca   16  15h         11   14  2.2     14          11   
35  Spain - Foz, La Charca   16  17h         10   14    2     14          11   
36  Spain - Foz, La Charca   16  19h          9   12  1.9     14          11   
37  Spain - Foz, La Charca   16  22h          6   10  1.8     14          10   
38  Spain - Foz, La Charca   17  04h          4    8  1.4     14           8   
39  Spain - Foz, La Charca   17  06h          4    7  1.3     14           8   
40  Spain - Foz, La Charca   17  08h          4    7  1.2     14           8   
41  Spain - Foz, La Charca   17  10h          4    8  1.1     14           8   
42  Spain - Foz, La Charca   17  12h          4   10    1     14          11   
43  Spain - Foz, La Charca   17  14h          4   11  0.9     14          13   
44  Spain - Foz, La Charca   17  16h          3   10  0.9     14          14   
45  Spain - Foz, La Charca   17  18h          4    7  0.8     14          12   
46  Spain - Foz, La Charca   17  20h          4    6  0.8     14          11   
47  Spain - Foz, La Charca   17  22h          5    7  0.7     14          10   
48  Spain - Foz, La Charca   18  04h         11   27  0.7     14          13   
49  Spain - Foz, La C

In [24]:
lst_playas7=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in links7)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   6 out of  10 | elapsed:  1.0min remaining:   40.4s
[Parallel(n_jobs=-1)]: Done  10 out of  10 | elapsed:  1.5min finished


In [25]:
playas7=pd.concat(lst_playas7)
playas7

Beach Date Hour Wind_speed Gust Wave Period  \
0            Spain - Santa Comba   13  07h         11   20  2.7     14   
1            Spain - Santa Comba   13  09h         11   19  2.5     14   
2            Spain - Santa Comba   13  11h         10   18  2.5     14   
3            Spain - Santa Comba   13  13h          9   15  2.4     14   
4            Spain - Santa Comba   13  15h         10   19  2.3     14   
5            Spain - Santa Comba   13  17h         11   19  2.3     14   
6            Spain - Santa Comba   13  19h         12   22  2.4     14   
7            Spain - Santa Comba   13  21h         13   21  2.4     14   
8            Spain - Santa Comba   14  03h         16   26  2.7     14   
9            Spain - Santa Comba   14  05h         15   24  2.7     14   
10           Spain - Santa Comba   14  07h         16   27  2.7     14   
11           Spain - Santa Comba   14  09h         17   30  2.8     14   
12           Spain - Santa Comba   14  11h         18   30    3     14   
13           Spain - Santa Comba   14  13h         16   29  3.2     14   
14           Spain - Santa Comba   14  15h         14   24  3.4     14   
15           Spain - Santa Comba   14  17h         14   25  3.5     14   
16           Spain - Santa Comba   14  19h         15   25  3.5     14   
17           Spain - Santa Comba   14  21h         11   20  3.3     14   
18           Spain - Santa Comba   15  03h          9   14  2.7     14   
19           Spain - Santa Comba   15  05h          8   12  2.6     14   
20           Spain - Santa Comba   15  07h          8   12  2.5     14   
21           Spain - Santa Comba   15  09h          8   13  2.4     14   
22           Spain - Santa Comba   15  11h          8   14  2.4     14   
23           Spain - Santa Comba   15  13h          8   12  2.5     14   
24           Spain - Santa Comba   15  15h          5   10  2.5     14   
25           Spain - Santa Comba   15  17h          5    7  2.6     14   
26           Spain - Santa Comba   15  19h          5    7  2.7     14   
27           Spain - Santa Comba   15  21h          4    6    3     14   
28           Spain - Santa Comba   16  03h          8   13  3.3     14   
29           Spain - Santa Comba   16  05h         12   20  3.3     14   
30           Spain - Santa Comba   16  07h         14   22    3     14   
31           Spain - Santa Comba   16  09h         15   22    3     14   
32           Spain - Santa Comba   16  11h         13   20  2.8     14   
33           Spain - Santa Comba   16  13h         14   20  2.5     14   
34           Spain - Santa Comba   16  15h         12   15  2.3     14   
35           Spain - Santa Comba   16  17h         11   15  2.1     14   
36           Spain - Santa Comba   16  19h         10   15    2     14   
37           Spain - Santa Comba   16  22h          6    8  1.8     14   
38           Spain - Santa Comba   17  04h          5    6  1.4     14   
39           Spain - Santa Comba   17  06h          6    7  1.3     14   
40           Spain - Santa Comba   17  08h          7    9  1.2     14   
41           Spain - Santa Comba   17  10h          9   13  1.2     14   
42           Spain - Santa Comba   17  12h          9   13  1.1     14   
43           Spain - Santa Comba   17  14h          9   14  1.1     14   
44           Spain - Santa Comba   17  16h          8   14    1     14   
45           Spain - Santa Comba   17  18h          9   15    1     14   
46           Spain - Santa Comba   17  20h         10   17    1     14   
47           Spain - Santa Comba   17  22h         12   21  1.1     14   
48           Spain - Santa Comba   18  04h         19   32  1.9     14   
49           Spain - Santa Comba   18  06h         18   31  2.1     14   
50           Spain - Santa Comba   18  08h         20   38  2.3     14   
51           Spain - Santa Comba   18  10h         22   42  2.6     14   
52           Spain - Santa Comba   18  12h         24   42  2.8     14   
53           Spain - Santa Comb

In [50]:
lst_playasCN=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksCN)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   4 out of   9 | elapsed:   58.6s remaining:  1.2min
[Parallel(n_jobs=-1)]: Done   9 out of   9 | elapsed:  1.5min finished


In [51]:
playasCN=pd.concat(lst_playasCN)
playasCN

Beach Date Hour Wind_speed Gust Wave Period  \
0   Spain - Puerto de la Cruz   13  06h          4    5  1.6     12   
1   Spain - Puerto de la Cruz   13  08h          5    7  1.6     12   
2   Spain - Puerto de la Cruz   13  10h          3    5  1.6     12   
3   Spain - Puerto de la Cruz   13  12h          3    5  1.6     12   
4   Spain - Puerto de la Cruz   13  14h          4    5  1.6     12   
5   Spain - Puerto de la Cruz   13  16h          3    5  1.6     12   
6   Spain - Puerto de la Cruz   13  18h          1    3  1.6     12   
7   Spain - Puerto de la Cruz   13  20h          3    5  1.6     12   
8   Spain - Puerto de la Cruz   13  22h          4    5  1.7     12   
9   Spain - Puerto de la Cruz   14  03h          6   10  1.8     12   
10  Spain - Puerto de la Cruz   14  05h          7   12  1.9     12   
11  Spain - Puerto de la Cruz   14  07h          6   15  1.8     12   
12  Spain - Puerto de la Cruz   14  09h          7   13  1.8     12   
13  Spain - Puerto de la Cruz   14  11h          8   12  1.7     12   
14  Spain - Puerto de la Cruz   14  13h          9   12  1.7     12   
15  Spain - Puerto de la Cruz   14  15h          8   12  1.8     12   
16  Spain - Puerto de la Cruz   14  17h          6    9  1.8     12   
17  Spain - Puerto de la Cruz   14  19h          3    7  1.8     12   
18  Spain - Puerto de la Cruz   14  21h          3    6  1.8     12   
19  Spain - Puerto de la Cruz   15  03h          4    8    2     12   
20  Spain - Puerto de la Cruz   15  05h          4    8  2.1     12   
21  Spain - Puerto de la Cruz   15  07h          4    8  2.2     12   
22  Spain - Puerto de la Cruz   15  09h          5    8  2.3     12   
23  Spain - Puerto de la Cruz   15  11h          5    8  2.4     12   
24  Spain - Puerto de la Cruz   15  13h          6    9  2.5     12   
25  Spain - Puerto de la Cruz   15  15h          7    9  2.5     12   
26  Spain - Puerto de la Cruz   15  17h          6    8  2.6     12   
27  Spain - Puerto de la Cruz   15  19h          4    7  2.6     12   
28  Spain - Puerto de la Cruz   15  21h          3    6  2.7     12   
29  Spain - Puerto de la Cruz   16  03h          3    5    3     12   
30  Spain - Puerto de la Cruz   16  05h          3    6  3.1     12   
31  Spain - Puerto de la Cruz   16  07h          1    4  3.1     12   
32  Spain - Puerto de la Cruz   16  09h          1    3  3.1     12   
33  Spain - Puerto de la Cruz   16  11h          3    4  3.1     12   
34  Spain - Puerto de la Cruz   16  15h          5    6  2.8     12   
35  Spain - Puerto de la Cruz   16  18h          4    5  2.6     12   
36  Spain - Puerto de la Cruz   16  21h          3    5  2.4     12   
37  Spain - Puerto de la Cruz   17  03h          3    5  2.1     12   
38  Spain - Puerto de la Cruz   17  06h          5    6    2     12   
39  Spain - Puerto de la Cruz   17  09h          4    6  1.9     12   
40  Spain - Puerto de la Cruz   17  12h          6    8  1.8     12   
41  Spain - Puerto de la Cruz   17  15h          6    6  1.8     12   
42  Spain - Puerto de la Cruz   17  18h          3    4  1.7     12   
43  Spain - Puerto de la Cruz   17  21h          3    5  1.6     12   
44  Spain - Puerto de la Cruz   18  03h          3    4  1.5     12   
45  Spain - Puerto de la Cruz   18  06h          3    4  1.4     12   
46  Spain - Puerto de la Cruz   18  09h          4    4  1.3     12   
47  Spain - Puerto de la Cruz   18  12h          5    6  1.2     12   
48  Spain - Puerto de la Cruz   18  15h          5    6  1.3     12   
49  Spain - Puerto de la Cruz   18  18h          3    5  1.7     12   
50  Spain - Puerto de la Cruz   18  21h          1    4  2.3     12   
51  Spain - Puerto de la Cruz   19  03h          3    4  2.7     12   
52  Spain - Puerto de la Cruz   19  06h          3    4  2.7     12   
53  Spain - Puerto de la Cruz   19  09h          3    4  2.6     12   
54  Spain - Puerto de la Cruz   19  12h          6    6  2.5     12   
55  Spain - Puerto de la Cruz   19  15h         

In [35]:
#lst_playasCN1=tirania('https://www.windguru.cz/103501')

In [36]:
#lst_playasCN1

In [37]:
#lst_playasCN3=tirania('https://www.windguru.cz/501283')

In [38]:
#lst_playasCN3

In [39]:
#lst_playasCN4=tirania('https://www.windguru.cz/49328' )
#lst_playasCN4

In [40]:
#lst_playasCN5=tirania('https://www.windguru.cz/501281')

In [41]:
#lst_playasCN5

In [52]:
playasN= pd.concat([playas, playas2, playas3, playas4, playas5, playas6, playas7, playasCN], axis=0)
playasN

Beach Date Hour Wind_speed Gust  \
0                              Spain - Hondarribia   13  07h          7   12   
1                              Spain - Hondarribia   13  09h          4    6   
2                              Spain - Hondarribia   13  11h          4    6   
3                              Spain - Hondarribia   13  13h          3    7   
4                              Spain - Hondarribia   13  15h          4    7   
5                              Spain - Hondarribia   13  17h          7   11   
6                              Spain - Hondarribia   13  19h          8   15   
7                              Spain - Hondarribia   13  21h          6   12   
8                              Spain - Hondarribia   14  03h          6   13   
9                              Spain - Hondarribia   14  05h          4   10   
10                             Spain - Hondarribia   14  07h          4    7   
11                             Spain - Hondarribia   14  09h          5    7   
12                             Spain - Hondarribia   14  11h          6   11   
13                             Spain - Hondarribia   14  13h          4    9   
14                             Spain - Hondarribia   14  15h          3    8   
15                             Spain - Hondarribia   14  17h          6    9   
16                             Spain - Hondarribia   14  19h          7   13   
17                             Spain - Hondarribia   14  21h          6   11   
18                             Spain - Hondarribia   15  03h          7   13   
19                             Spain - Hondarribia   15  05h          7   13   
20                             Spain - Hondarribia   15  07h          7   12   
21                             Spain - Hondarribia   15  09h          8   14   
22                             Spain - Hondarribia   15  11h          9   16   
23                             Spain - Hondarribia   15  13h          8   14   
24                             Spain - Hondarribia   15  15h          8   13   
25                             Spain - Hondarribia   15  17h          8   14   
26                             Spain - Hondarribia   15  19h          6   12   
27                             Spain - Hondarribia   15  21h          6   10   
28                             Spain - Hondarribia   16  03h          6   12   
29                             Spain - Hondarribia   16  05h          5   12   
30                             Spain - Hondarribia   16  07h          7   11   
31                             Spain - Hondarribia   16  09h          8   13   
32                             Spain - Hondarribia   16  11h          8   11   
33                             Spain - Hondarribia   16  13h          9   13   
34                             Spain - Hondarribia   16  15h          9   14   
35                             Spain - Hondarribia   16  17h         10   13   
36                             Spain - Hondarribia   16  19h          9   11   
37                             Spain - Hondarribia   16  22h          4    6   
38                             Spain - Hondarribia   17  04h          3    4   
39                             Spain - Hondarribia   17  06h          3    5   
40                             Spain - Hondarribia   17  08h          3    5   
41                             Spain - Hondarribia   17  10h          3    5   
42                             Spain - Hondarribia   17  12h          2    5   
43                             Spain - Hondarribia   17  14h          2    5   
44                             Spain - Hondarribia   17  16h          3    5   
45                             Spain - Hondarribia   17  18h          4    5   
46                             Spain - Hondarribia   17  20h          5    6   
47                             Spain - Hondarribia   17  22h          5    6   
48                             Spain - Hondarribia   18  04h          8   10   
49                             Spain - Hondar

In [53]:
playasN.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasN.csv', index=False, index_label=False)


In [54]:
linksO=['https://www.windguru.cz/48730',
       'https://www.windguru.cz/48731',
       'https://www.windguru.cz/501109',
       'https://www.windguru.cz/501110',
       'https://www.windguru.cz/48733',
       'https://www.windguru.cz/48735',
       'https://www.windguru.cz/48736',
       'https://www.windguru.cz/501116',
       'https://www.windguru.cz/501118',
       'https://www.windguru.cz/128497',
       'https://www.windguru.cz/718895',
       'https://www.windguru.cz/501119',
       'https://www.windguru.cz/501120',
       'https://www.windguru.cz/48738',
       'https://www.windguru.cz/153771',
        'https://www.windguru.cz/501113',
       'https://www.windguru.cz/501114',
       'https://www.windguru.cz/501115',
       'https://www.windguru.cz/48739',
       'https://www.windguru.cz/48741',
       'https://www.windguru.cz/1066',
       'https://www.windguru.cz/48742',
       'https://www.windguru.cz/48743']

In [57]:
lst_playasO=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksO)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  23 out of  23 | elapsed:  2.9min finished


In [58]:
playasO=pd.concat(lst_playasO)
playasO

Beach Date Hour Wind_speed Gust Wave Period  \
0              Spain - Nemina   13  10h         11   20  3.3     13   
1              Spain - Nemina   13  12h         10   19  3.2     13   
2              Spain - Nemina   13  14h         11   20  3.1     13   
3              Spain - Nemina   13  16h         12   21  3.1     13   
4              Spain - Nemina   13  18h         11   21  3.1     13   
5              Spain - Nemina   13  20h         12   21  3.1     13   
6              Spain - Nemina   13  22h         14   24  3.1     13   
7              Spain - Nemina   14  03h         16   26  3.3     13   
8              Spain - Nemina   14  05h         16   28  3.4     13   
9              Spain - Nemina   14  07h         17   29  3.5     13   
10             Spain - Nemina   14  09h         18   30  3.8     13   
11             Spain - Nemina   14  11h         18   32  4.1     13   
12             Spain - Nemina   14  13h         18   31  4.3     13   
13             Spain - Nemina   14  15h         17   29  4.5     13   
14             Spain - Nemina   14  17h         20   31  4.5     13   
15             Spain - Nemina   14  19h         16   24  4.4     13   
16             Spain - Nemina   14  21h         13   23  4.2     13   
17             Spain - Nemina   15  03h          9   17  3.5     13   
18             Spain - Nemina   15  05h         10   16  3.5     13   
19             Spain - Nemina   15  07h         10   17  3.5     13   
20             Spain - Nemina   15  09h          9   16  3.5     13   
21             Spain - Nemina   15  11h          9   16  3.5     13   
22             Spain - Nemina   15  13h          9   16  3.5     13   
23             Spain - Nemina   15  15h          7   12  3.5     13   
24             Spain - Nemina   15  17h          5   10  3.4     13   
25             Spain - Nemina   15  19h          6    9  3.3     13   
26             Spain - Nemina   15  21h          5    8  3.3     13   
27             Spain - Nemina   16  03h          7   10  3.1     13   
28             Spain - Nemina   16  05h          9   15  3.1     13   
29             Spain - Nemina   16  07h         11   20    3     13   
30             Spain - Nemina   16  09h         13   24  2.9     13   
31             Spain - Nemina   16  11h         14   24  2.8     13   
32             Spain - Nemina   16  13h         13   21  2.5     13   
33             Spain - Nemina   16  15h         10   14  2.3     13   
34             Spain - Nemina   16  17h          8   14  2.2     13   
35             Spain - Nemina   16  19h          9   16    2     13   
36             Spain - Nemina   16  22h          6    9  1.8     13   
37             Spain - Nemina   17  04h          7   10  1.5     13   
38             Spain - Nemina   17  06h          8   11  1.4     13   
39             Spain - Nemina   17  08h          8   12  1.3     13   
40             Spain - Nemina   17  10h          9   13  1.2     13   
41             Spain - Nemina   17  12h         13   19  1.2     13   
42             Spain - Nemina   17  14h         16   23  1.4     13   
43             Spain - Nemina   17  16h         19   27  1.6     13   
44             Spain - Nemina   17  18h         20   29  1.7     13   
45             Spain - Nemina   17  20h         21   31  1.8     13   
46             Spain - Nemina   17  22h         23   35    2     13   
47             Spain - Nemina   18  04h         28   43  2.9     13   
48             Spain - Nemina   18  06h         25   41  3.1     13   
49             Spain - Nemina   18  08h         27   43  3.4     13   
50             Spain - Nemina   18  10h         28   44  3.8     13   
51             Spain - Nemina   18  12h         29   45  4.1     13   
52             Spain - Nemina   18  14h         29   46  4.4     13   
53             Spain - Nemina   18  16h         28   45  4.5     13   
54             Spain - Nemina   18  18h         30   46  4.7     13   
55             Spain - Nemina   18  20h         

In [59]:
playasO.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasO.csv', index=False, index_label=False)


In [21]:
linksSO=['https://www.windguru.cz/501074',
         'https://www.windguru.cz/48745',
        'https://www.windguru.cz/48748',
        'https://www.windguru.cz/39598',
        'https://www.windguru.cz/48755',
        'https://www.windguru.cz/38193',
        'https://www.windguru.cz/48766',
        'https://www.windguru.cz/5691',
        'https://www.windguru.cz/48769',
        'https://www.windguru.cz/48780',
        'https://www.windguru.cz/48762'
        'https://www.windguru.cz/799776']

In [25]:
lst_playasSO=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksSO)




[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   8 out of  11 | elapsed:  1.1min remaining:   25.0s


NoSuchElementException: Message: no such element: Unable to locate element: {"method":"xpath","selector":"//*[@id="tabid_0_0_dates"]"}
  (Session info: chrome=108.0.5359.99)
Stacktrace:
Backtrace:
	(No symbol) [0x00BFF243]
	(No symbol) [0x00B87FD1]
	(No symbol) [0x00A7D04D]
	(No symbol) [0x00AAC0B0]
	(No symbol) [0x00AAC22B]
	(No symbol) [0x00ADE612]
	(No symbol) [0x00AC85D4]
	(No symbol) [0x00ADC9EB]
	(No symbol) [0x00AC8386]
	(No symbol) [0x00AA163C]
	(No symbol) [0x00AA269D]
	GetHandleVerifier [0x00E99A22+2655074]
	GetHandleVerifier [0x00E8CA24+2601828]
	GetHandleVerifier [0x00CA8C0A+619850]
	GetHandleVerifier [0x00CA7830+614768]
	(No symbol) [0x00B905FC]
	(No symbol) [0x00B95968]
	(No symbol) [0x00B95A55]
	(No symbol) [0x00BA051B]
	BaseThreadInitThunk [0x753C6939+25]
	RtlGetFullPathName_UEx [0x77058FD2+1218]
	RtlGetFullPathName_UEx [0x77058F9D+1165]


In [ ]:
playasSO=pd.concat(lst_playasSO)
playasSO

In [63]:
playasSO.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasSO.csv', index=False, index_label=False)

In [90]:


linksE=[#'https://www.windguru.cz/501057',
       #'https://www.windguru.cz/501050',
       #'https://www.windguru.cz/42069',
       #'https://www.windguru.cz/48878',
       #'https://www.windguru.cz/48879',
       #'https://www.windguru.cz/48846',
       #'https://www.windguru.cz/501038',
       #'https://www.windguru.cz/48869',
       #'https://www.windguru.cz/48851',
       #'https://www.windguru.cz/48890',
       #'https://www.windguru.cz/48882',
       'https://www.windguru.cz/48899',
       'https://www.windguru.cz/48897',
       'https://www.windguru.cz/48908']
       #'https://www.windguru.cz/48909']   

linksS=['https://www.windguru.cz/48790',
       'https://www.windguru.cz/48816',
       'https://www.windguru.cz/48817',
       'https://www.windguru.cz/501058',
       #'https://www.windguru.cz/48819',
       'https://www.windguru.cz/48811',
       'https://www.windguru.cz/48806']

linksCS=['https://www.windguru.cz/49354',
        'https://www.windguru.cz/49355',
        'https://www.windguru.cz/208234',
        'https://www.windguru.cz/49353',
        'https://www.windguru.cz/49346',
        'https://www.windguru.cz/49333',
        'https://www.windguru.cz/49332']

In [67]:
lst_playasCS=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksCS)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   7 out of   7 | elapsed:   59.8s finished


In [68]:
playasCS=pd.concat(lst_playasCS)
playasCS

Beach Date Hour Wind_speed Gust Wave Period  \
0         Spain - Las Americas   13  06h          3    4  0.8     11   
1         Spain - Las Americas   13  08h          3    4  0.8     11   
2         Spain - Las Americas   13  10h          3    4  0.8     11   
3         Spain - Las Americas   13  12h          5    6  0.8     11   
4         Spain - Las Americas   13  14h          6    7  0.8     11   
5         Spain - Las Americas   13  16h          6    8  0.9     11   
6         Spain - Las Americas   13  18h          5    6  0.9     11   
7         Spain - Las Americas   13  20h          5    6  0.9     11   
8         Spain - Las Americas   13  22h          9   10  0.9     11   
9         Spain - Las Americas   14  03h          9   11  0.9     11   
10        Spain - Las Americas   14  05h         14   18    1     11   
11        Spain - Las Americas   14  07h         15   19    1     11   
12        Spain - Las Americas   14  09h         15   19    1     11   
13        Spain - Las Americas   14  11h         16   18    1     11   
14        Spain - Las Americas   14  13h         19   21    1     11   
15        Spain - Las Americas   14  15h         19   23  1.1     11   
16        Spain - Las Americas   14  17h         19   23  1.3     11   
17        Spain - Las Americas   14  19h         15   17  1.3     11   
18        Spain - Las Americas   14  21h         15   17  1.2     11   
19        Spain - Las Americas   15  03h          9   12  1.3     11   
20        Spain - Las Americas   15  05h          7   10  1.3     11   
21        Spain - Las Americas   15  07h          6    9  1.4     11   
22        Spain - Las Americas   15  09h          6    8  1.3     11   
23        Spain - Las Americas   15  11h          8   10  1.3     11   
24        Spain - Las Americas   15  13h          9   11  1.5     11   
25        Spain - Las Americas   15  15h         10   12  1.4     11   
26        Spain - Las Americas   15  17h          8   11  1.5     11   
27        Spain - Las Americas   15  19h          4    5  1.5     11   
28        Spain - Las Americas   15  21h          3    4  1.4     11   
29        Spain - Las Americas   16  03h          6    7  1.6     11   
30        Spain - Las Americas   16  05h          8   10  1.7     11   
31        Spain - Las Americas   16  07h          3    5  1.8     11   
32        Spain - Las Americas   16  09h          3    5  1.8     11   
33        Spain - Las Americas   16  11h          2    5  1.7     11   
34        Spain - Las Americas   16  15h          3    4  1.6     11   
35        Spain - Las Americas   16  18h          2    3  1.5     11   
36        Spain - Las Americas   16  21h          2    3  1.4     11   
37        Spain - Las Americas   17  03h          3    5  1.2     11   
38        Spain - Las Americas   17  06h          3    5  1.1     11   
39        Spain - Las Americas   17  09h          4    8    1     11   
40        Spain - Las Americas   17  12h          8   12  1.1     11   
41        Spain - Las Americas   17  15h          9   10    1     11   
42        Spain - Las Americas   17  18h          4    6  0.9     11   
43        Spain - Las Americas   17  21h          3    6  0.8     11   
44        Spain - Las Americas   18  03h          5    7  0.8     11   
45        Spain - Las Americas   18  06h          6    8  0.7     11   
46        Spain - Las Americas   18  09h          7    8  0.7     11   
47        Spain - Las Americas   18  12h          7    7  0.7     11   
48        Spain - Las Americas   18  15h          4    5  0.6     11   
49        Spain - Las Americas   18  18h          3    4  0.7     11   
50        Spain - Las Americas   18  21h          3    3  0.9     11   
51        Spain - Las Americas   19  03h          2    5  1.1     11   
52        Spain - Las Americas   19  06h          4    5  1.1     11   
53        Spain - Las Americas   19  09h          3    4  1.1     11   
54        Spain - Las Americas   19  12h          2    3  1.1    

In [72]:
lst_playasS=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksS)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   6 out of   6 | elapsed:   49.5s finished


In [73]:
playasS1=pd.concat(lst_playasS)
playasS1

Beach Date Hour Wind_speed Gust Wave Period Temperature  \
0        Spain - Cabopino   13  10h         19   33  1.5      5          18   
1        Spain - Cabopino   13  12h         20   36  1.8      5          18   
2        Spain - Cabopino   13  14h         23   38  2.1      5          18   
3        Spain - Cabopino   13  16h         23   38  2.2      5          18   
4        Spain - Cabopino   13  18h         21   36    2      5          19   
5        Spain - Cabopino   13  20h         22   38  1.9      5          19   
6        Spain - Cabopino   13  22h         17   31  1.9      5          18   
7        Spain - Cabopino   14  03h         13   19  1.4      5          18   
8        Spain - Cabopino   14  05h         10   16  1.4      5          17   
9        Spain - Cabopino   14  07h          9   14  1.2      5          17   
10       Spain - Cabopino   14  09h         11   17  1.1      5          17   
11       Spain - Cabopino   14  11h         15   22  1.1      5          17   
12       Spain - Cabopino   14  13h         15   20  1.1      5          17   
13       Spain - Cabopino   14  15h         12   17    1      5          17   
14       Spain - Cabopino   14  17h         11   16  0.9      5          17   
15       Spain - Cabopino   14  19h         11   17    1      5          17   
16       Spain - Cabopino   14  21h         14   24  1.1      5          17   
17       Spain - Cabopino   15  03h         12   20  1.5      5          16   
18       Spain - Cabopino   15  05h         14   23  1.6      5          16   
19       Spain - Cabopino   15  07h         13   18  1.3      5          15   
20       Spain - Cabopino   15  09h         14   21  1.1      5          15   
21       Spain - Cabopino   15  11h         12   17  0.9      5          15   
22       Spain - Cabopino   15  13h         14   19  0.9      5          15   
23       Spain - Cabopino   15  15h         12   19    1      5          15   
24       Spain - Cabopino   15  17h         12   18  1.5      5          15   
25       Spain - Cabopino   15  19h         12   17  1.3      5          15   
26       Spain - Cabopino   15  21h         11   17  1.4      5          14   
27       Spain - Cabopino   16  03h          6    9    1      5          14   
28       Spain - Cabopino   16  05h          5    8  0.9      5          13   
29       Spain - Cabopino   16  07h          7   10    1      5          14   
30       Spain - Cabopino   16  09h         11   18    1      5          14   
31       Spain - Cabopino   16  11h         14   22    1      5          15   
32       Spain - Cabopino   16  13h         16   24  1.1      5          16   
33       Spain - Cabopino   16  15h         18   25  1.2      5          16   
34       Spain - Cabopino   16  17h         15   21  1.2      5          16   
35       Spain - Cabopino   16  19h         13   18    1      5          16   
36       Spain - Cabopino   16  22h          4    5  0.8      5          15   
37       Spain - Cabopino   17  04h          4    6  0.6      5          14   
38       Spain - Cabopino   17  06h          4    6  0.6      5          13   
39       Spain - Cabopino   17  08h          4    6  0.6      5          14   
40       Spain - Cabopino   17  10h          4    6  0.6      5          14   
41       Spain - Cabopino   17  12h          4    5  0.5      5          15   
42       Spain - Cabopino   17  14h          4    6  0.5      5          16   
43       Spain - Cabopino   17  16h          5    6  0.4      5          17   
44       Spain - Cabopino   17  18h          4    4  0.4      5          16   
45       Spain - Cabopino   17  20h          3    3  0.3      5          15   
46       Spain - Cabopino   17  22h          3    3  0.3      5          15   
47       Spain - Cabopino   18  04h          5    6  0.2      5          13   
48       Spain - Cabopino   18  06h          6    6  0.2      5          14   
49       Spain - Cabopino   18  08h          7    8  0.3      5       

In [74]:
playasS= pd.concat([playasS1, playasCS], axis=0)
playasS

Beach Date Hour Wind_speed Gust Wave Period  \
0             Spain - Cabopino   13  10h         19   33  1.5      5   
1             Spain - Cabopino   13  12h         20   36  1.8      5   
2             Spain - Cabopino   13  14h         23   38  2.1      5   
3             Spain - Cabopino   13  16h         23   38  2.2      5   
4             Spain - Cabopino   13  18h         21   36    2      5   
5             Spain - Cabopino   13  20h         22   38  1.9      5   
6             Spain - Cabopino   13  22h         17   31  1.9      5   
7             Spain - Cabopino   14  03h         13   19  1.4      5   
8             Spain - Cabopino   14  05h         10   16  1.4      5   
9             Spain - Cabopino   14  07h          9   14  1.2      5   
10            Spain - Cabopino   14  09h         11   17  1.1      5   
11            Spain - Cabopino   14  11h         15   22  1.1      5   
12            Spain - Cabopino   14  13h         15   20  1.1      5   
13            Spain - Cabopino   14  15h         12   17    1      5   
14            Spain - Cabopino   14  17h         11   16  0.9      5   
15            Spain - Cabopino   14  19h         11   17    1      5   
16            Spain - Cabopino   14  21h         14   24  1.1      5   
17            Spain - Cabopino   15  03h         12   20  1.5      5   
18            Spain - Cabopino   15  05h         14   23  1.6      5   
19            Spain - Cabopino   15  07h         13   18  1.3      5   
20            Spain - Cabopino   15  09h         14   21  1.1      5   
21            Spain - Cabopino   15  11h         12   17  0.9      5   
22            Spain - Cabopino   15  13h         14   19  0.9      5   
23            Spain - Cabopino   15  15h         12   19    1      5   
24            Spain - Cabopino   15  17h         12   18  1.5      5   
25            Spain - Cabopino   15  19h         12   17  1.3      5   
26            Spain - Cabopino   15  21h         11   17  1.4      5   
27            Spain - Cabopino   16  03h          6    9    1      5   
28            Spain - Cabopino   16  05h          5    8  0.9      5   
29            Spain - Cabopino   16  07h          7   10    1      5   
30            Spain - Cabopino   16  09h         11   18    1      5   
31            Spain - Cabopino   16  11h         14   22    1      5   
32            Spain - Cabopino   16  13h         16   24  1.1      5   
33            Spain - Cabopino   16  15h         18   25  1.2      5   
34            Spain - Cabopino   16  17h         15   21  1.2      5   
35            Spain - Cabopino   16  19h         13   18    1      5   
36            Spain - Cabopino   16  22h          4    5  0.8      5   
37            Spain - Cabopino   17  04h          4    6  0.6      5   
38            Spain - Cabopino   17  06h          4    6  0.6      5   
39            Spain - Cabopino   17  08h          4    6  0.6      5   
40            Spain - Cabopino   17  10h          4    6  0.6      5   
41            Spain - Cabopino   17  12h          4    5  0.5      5   
42            Spain - Cabopino   17  14h          4    6  0.5      5   
43            Spain - Cabopino   17  16h          5    6  0.4      5   
44            Spain - Cabopino   17  18h          4    4  0.4      5   
45            Spain - Cabopino   17  20h          3    3  0.3      5   
46            Spain - Cabopino   17  22h          3    3  0.3      5   
47            Spain - Cabopino   18  04h          5    6  0.2      5   
48            Spain - Cabopino   18  06h          6    6  0.2      5   
49            Spain - Cabopino   18  08h          7    8  0.3      5   
50            Spain - Cabopino   18  10h          8   10  0.3      5   
51            Spain - Cabopino   18  12h         10   12  0.4      5   
52            Spain - Cabopino   18  14h          9   12  0.4      5   
53            Spain - Cabopino   18  16h          9   11  0.5      5   
54            Spain - Cabopino   18  18h          8   10  0.5    

In [75]:
playasS.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasS.csv', index=False, index_label=False)

In [91]:
lst_playasE=Parallel(n_jobs=-1, verbose=True)(delayed(tirania)(url) for url in linksE)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done   3 out of   3 | elapsed:   36.6s finished


In [92]:
playasE=pd.concat(lst_playasE)
playasE

Beach Date Hour Wind_speed Gust Wave Period Temperature  \
0   Spain - Sant Martí   13  10h          3    5    1      6           8   
1   Spain - Sant Martí   13  12h          2    3    1      6          11   
2   Spain - Sant Martí   13  14h          2    3    1      6          12   
3   Spain - Sant Martí   13  16h          2    4    1      6          13   
4   Spain - Sant Martí   13  18h          3    6    1      6          12   
5   Spain - Sant Martí   13  20h          3    4  0.9      6          11   
6   Spain - Sant Martí   13  22h          3    6  0.9      6          11   
7   Spain - Sant Martí   14  03h          5    8    1      6          11   
8   Spain - Sant Martí   14  05h          5    8  1.1      6          11   
9   Spain - Sant Martí   14  07h          4   10  1.2      6          11   
10  Spain - Sant Martí   14  09h          7    9  1.4      6          12   
11  Spain - Sant Martí   14  11h          4    8  1.5      6          13   
12  Spain - Sant Martí   14  13h          6    9  1.4      6          13   
13  Spain - Sant Martí   14  15h          4    6  1.3      6          14   
14  Spain - Sant Martí   14  17h          4    5  1.2      6          14   
15  Spain - Sant Martí   14  19h          4    7  1.1      6          13   
16  Spain - Sant Martí   14  21h          6    8    1      6          12   
17  Spain - Sant Martí   15  03h          3    4  0.7      6          11   
18  Spain - Sant Martí   15  05h          3    3  0.7      6          10   
19  Spain - Sant Martí   15  07h          4    5  0.6      6          10   
20  Spain - Sant Martí   15  09h          3    5  0.6      6          11   
21  Spain - Sant Martí   15  11h          3    6  0.6      6          12   
22  Spain - Sant Martí   15  13h          4    7  0.6      6          15   
23  Spain - Sant Martí   15  15h          8   11  0.7      6          15   
24  Spain - Sant Martí   15  17h          8   12  0.9      6          14   
25  Spain - Sant Martí   15  19h          5    7    1      6          13   
26  Spain - Sant Martí   15  21h          3    5  0.9      6          12   
27  Spain - Sant Martí   16  03h          4    5  0.9      6          10   
28  Spain - Sant Martí   16  05h          3    4  0.8      6          10   
29  Spain - Sant Martí   16  07h          4    4  0.7      6          10   
30  Spain - Sant Martí   16  09h          3    3  0.7      6          10   
31  Spain - Sant Martí   16  11h          3    3  0.7      6          13   
32  Spain - Sant Martí   16  13h          3    4  0.6      6          14   
33  Spain - Sant Martí   16  15h          5    5  0.6      6          14   
34  Spain - Sant Martí   16  17h          4    5  0.6      6          13   
35  Spain - Sant Martí   16  19h          4    5  0.6      6          12   
36  Spain - Sant Martí   16  22h          4    5  0.6      6          11   
37  Spain - Sant Martí   17  04h          4    5  0.6      6          10   
38  Spain - Sant Martí   17  06h          4    5  0.6      6          10   
39  Spain - Sant Martí   17  08h          4    5  0.6      6           9   
40  Spain - Sant Martí   17  10h          4    5  0.5      6           9   
41  Spain - Sant Martí   17  12h          5    6  0.4      6          11   
42  Spain - Sant Martí   17  14h          6    6  0.4      6          12   
43  Spain - Sant Martí   17  16h          6    7  0.4      6          13   
44  Spain - Sant Martí   17  18h          5    6  0.4      6          12   
45  Spain - Sant Martí   17  20h          5    5  0.4      6          11   
46  Spain - Sant Martí   17  22h          4    4  0.3      6          11   
47  Spain - Sant Martí   18  04h          3    3  0.2      6          10   
48  Spain - Sant Martí   18  06h          3    3  0.2      6           9   
49  Spain - Sant Martí   18  08h          4    4  0.2      6           8   
50  Spain - Sant Martí   18  10h          3    4  0.2      6          10   
51  Spain - Sant Martí   18  12h          5    9  0.2      6     

In [93]:
playasE.to_csv(r'C:\Users\Ari\desktop\ironhack\WaveFinder_Project\csv\playasE.csv', index=False, index_label=False)